In [1]:
import os
import ast
import spacy
import pandas as pd
import numpy as np
import statistics
from tqdm import tqdm
from clean_text import *
from stop_words import *

nlp = spacy.load("en_core_web_sm")
tqdm.pandas()

/Users/lingyaoli/Library/Python/3.9/lib/python/site-packages/urllib3/__init__.py:35: NotOpenSSLWarning: urllib3 v2 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(
[nltk_data] Downloading package punkt to /Users/lingyaoli/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/lingyaoli/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/lingyaoli/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/lingyaoli/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [2]:
import matplotlib.pyplot as plt
import seaborn as sns
from matplotlib import rcParams
import matplotlib.colors as mcolors

rcParams['figure.dpi'] = 500
rcParams['savefig.dpi'] = 500
rcParams['font.family'] = 'Serif'
rcParams['font.size'] = 18
rcParams['axes.labelsize'] = 18
rcParams['axes.titlesize'] = 18
rcParams['xtick.labelsize'] = 18
rcParams['ytick.labelsize'] = 18
rcParams['legend.fontsize'] = 18
rcParams['figure.titlesize'] = 18

In [ ]:
read_dir = "accessible-review-results"
files = [file for file in os.listdir(read_dir) if file.endswith('.jsonl')]
files = sorted(files)

review_dfs = list()

for file in files:
    filepath = os.path.join(read_dir, file)
    state_df = pd.read_json(filepath, lines=True)
    review_dfs.append(state_df)

review_df = pd.concat(review_dfs)
review_df.head(5)

In [ ]:
review_df['clean_target_text'] = review_df['target_text'].progress_apply(lambda x: clean_text(x))
review_df.head(5)

### Map Categories

In [3]:
mapping_df = pd.read_excel('places_summary.xlsx')
mapping_df = mapping_df.astype(str)
naics3_to_category = dict(zip(mapping_df['naics_code'], mapping_df['Categories']))
naics3_to_title = dict(zip(mapping_df['naics_code'], mapping_df['3-digit NAICS Title']))
naics3_to_naics2 = dict(zip(mapping_df['naics_code'], mapping_df['2-digit NAICS Code']))
naics2_to_title = dict(zip(mapping_df['2-digit NAICS Code'], mapping_df['2-digit NAICS Title']))
mapping_df

naics_code 2-digit NAICS Code  \
0         722                 72   
1         713                 71   
2         445                 44   
3         812                 81   
4         452                 45   
..        ...                ...   
90        313                 31   
91        425                 42   
92        521                 52   
93        316                 31   
94        213                 21   

                              2-digit NAICS Title 3-digit NAICS Code  \
0                 Accommodation and Food Services                722   
1             Arts, Entertainment, and Recreation                713   
2                                    Retail Trade                445   
3   Other Services (except Public Administration)                812   
4                                    Retail Trade                452   
..                                            ...                ...   
90                                  Manufacturing                313   
91                                Wholesale Trade                425   
92                          Finance and Insurance                521   
93                                  Manufacturing                316   
94  Mining, Quarrying, and Oil and Gas Extraction                213   

                                  3-digit NAICS Title        Categories  
0                   Food Services and Drinking Places        Restaurant  
1      Amusement, Gambling, and Recreation Industries        Recreation  
2                           Food and Beverage Stores       Retail Trade  
3                       Personal and Laundry Services  Personal Service  
4                         General Merchandise Stores       Retail Trade  
..                                                ...               ...  
90                                      Textile Mills               nan  
91  Wholesale Electronic Markets and Agents and Br...      Retail Trade  
92                  Monetary Authorities-Central Bank  Personal Service  
93           Leather and Allied Product Manufacturing               nan  
94                      Support Activities for Mining               nan  

[95 rows x 6 columns]

In [4]:
def get_category(df):
    df = df.dropna(subset=['naics_code'])
    df['3-digit-naics'] = df['naics_code'].astype(int).astype(str)
    df['2-digit-naics'] = df['3-digit-naics'].apply(lambda x: str(x)[:2])
    df['2-naics-title'] = df['2-digit-naics'].apply(lambda x: naics2_to_title.get(str(x), None))
    df['3-naics-title'] = df['3-digit-naics'].apply(lambda x: naics3_to_title.get(str(x), None))
    df['3-naics-category'] = df['3-digit-naics'].apply(lambda x: naics3_to_category.get(str(x), None))
    df['county-FIPS'] = df['BGFIPS'].apply(lambda x: str(x)[:5])
    return df

pois_df = pd.read_pickle('g_poisf.pkl')
pois_df = get_category(pois_df)

/Users/lingyaoli/Library/Python/3.9/lib/python/site-packages/geopandas/geodataframe.py:1819: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
/Users/lingyaoli/Library/Python/3.9/lib/python/site-packages/geopandas/geodataframe.py:1819: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
/Users/lingyaoli/Library/Python/3.9/lib/python/site-packages/geopandas/geodataframe.py:1819: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice fro

In [5]:
categories = ['Retail Trade', 'Recreation', 'Hotel', 'Personal Service',  'Restaurant', 'Health Care']

restaurant_df = pois_df[pois_df['3-naics-category'] == 'Restaurant']
retail_df = pois_df[pois_df['3-naics-category'] == 'Retail Trade']
service_df = pois_df[pois_df['3-naics-category'] == 'Personal Service']
recreation_df = pois_df[pois_df['3-naics-category'] == 'Recreation']
healthcare_df = pois_df[pois_df['3-naics-category'] == 'Health Care']
hotel_df = pois_df[pois_df['3-naics-category'] == 'Hotel']

restaurant_pois = list(set(restaurant_df['gmap_id'].tolist()))
retail_pois = list(set(retail_df['gmap_id'].tolist()))
service_pois = list(set(service_df['gmap_id'].tolist()))
recreation_pois = list(set(recreation_df['gmap_id'].tolist()))
healthcare_pois = list(set(healthcare_df['gmap_id'].tolist()))
hotel_pois = list(set(hotel_df['gmap_id'].tolist()))

In [6]:
review_df = pd.read_pickle('accessible-review-cleaned.pkl')
review_df.rename(columns={'clean_targe_text': 'clean_target_text'}, inplace=True)

In [7]:
restaurant_reviews = review_df[review_df['gmap_id'].isin(restaurant_pois)]
retail_reviews = review_df[review_df['gmap_id'].isin(retail_pois)]
service_reviews = review_df[review_df['gmap_id'].isin(service_pois)]
recreation_reviews = review_df[review_df['gmap_id'].isin(recreation_pois)]
healthcare_reviews = review_df[review_df['gmap_id'].isin(healthcare_pois)]
hotel_reviews = review_df[review_df['gmap_id'].isin(hotel_pois)]

print('restaurant reviews', len(restaurant_reviews))
print('retail reviews', len(retail_reviews))
print('service reviews', len(service_reviews))
print('recreation reviews', len(recreation_reviews))
print('apartment reviews', len(healthcare_reviews))
print('hotel reviews', len(hotel_reviews))

restaurant reviews 114070
retail reviews 160027
service reviews 41938
recreation reviews 113106
apartment reviews 33740
hotel reviews 115465


In [8]:
def generate_topic_words(review_df):
    """Generate words for the review data."""
    # Generate word frequencies for overall and each sentiment category
    def word_frequencies(series):
        word_counts = {}
        for text in series:
            for word in text.split():
                if word in word_counts:
                    word_counts[word] += 1
                else:
                    word_counts[word] = 1
        return word_counts

    # Calculate frequencies
    topic_freq = word_frequencies(review_df['clean_target_text'])
    pos_freq = word_frequencies(review_df[review_df['label'] == 'positive']['clean_target_text'])
    neg_freq = word_frequencies(review_df[review_df['label'] == 'negative']['clean_target_text'])
    neu_freq = word_frequencies(review_df[review_df['label'] == 'neutral']['clean_target_text'])

    # Convert frequencies to DataFrame
    topic_word = pd.DataFrame(list(topic_freq.items()), columns=['word', 'count'])
    topic_word['pos_count'] = topic_word['word'].map(pos_freq).fillna(0)
    topic_word['neg_count'] = topic_word['word'].map(neg_freq).fillna(0)
    topic_word['neu_count'] = topic_word['word'].map(neu_freq).fillna(0)

    # Calculate saliences and valences of words
    topic_word['salience'] = np.log10(topic_word['count'] + 1)  # Add 1 to avoid log(0)
    sum_count = (topic_word['pos_count'] + topic_word['neg_count'] + topic_word['neu_count'])
    topic_word['valence'] = (topic_word['pos_count'] - topic_word['neg_count']) / sum_count
    topic_word = topic_word.sort_values('salience', ascending=False)
    return topic_word

In [9]:
hotel_topic_word = generate_topic_words(hotel_reviews)
healthcare_topic_word = generate_topic_words(healthcare_reviews)
restaurant_topic_word = generate_topic_words(restaurant_reviews)
retail_topic_word = generate_topic_words(retail_reviews)
service_topic_word = generate_topic_words(service_reviews)
recreation_topic_word = generate_topic_words(recreation_reviews)

In [10]:
def extract_words(text):
    """Extract nouns and adjectives from the text."""
    doc = nlp(text)
    nouns_adjectives = [token.text for token in doc if (token.pos_ == "NOUN" or token.pos_ == "ADJ")]
    return " ".join(nouns_adjectives)

def filter_words(topic_word):
    """Filter words based on several identified conditions."""
    topic_word = topic_word[topic_word['word'].apply(lambda x: len(x) > 2)].reset_index(drop=True)
    topic_word = topic_word[~topic_word['word'].str.contains('|'.join(stopwords))]
    topic_word['is_noun_adj'] = topic_word['word'].apply(lambda x: bool(extract_words(x)))
    topic_word = topic_word[topic_word['is_noun_adj']]
    topic_word = topic_word.drop(columns=['is_noun_adj']).reset_index(drop=True)
    return topic_word

def select_top_words(topic_word, top_n):
    """Select the top words for plotting."""
    top_word = topic_word[:1000]
    top_word = filter_words(top_word)[:top_n]
    return top_word

In [11]:
restaurant_top_word = select_top_words(restaurant_topic_word, 40)
retail_top_word = select_top_words(retail_topic_word, 40)
service_top_word = select_top_words(service_topic_word, 40)
recreation_top_word = select_top_words(recreation_topic_word, 40)
hotel_top_word = select_top_words(hotel_topic_word, 40)
healthcare_top_word = select_top_words(healthcare_topic_word, 40)

### Generate figures

In [12]:
from adjustText import adjust_text

def plot_scatter(ax, top_word, title):
    """Plot the scatter plot."""
    ax.scatter(top_word['salience'], top_word['valence'],
               s=100,  # marker size
               marker='o',  # marker style
               edgecolors=['red' if valence <= 0 else 'blue' for valence in top_word['valence']],  # marker edge color
               facecolors='none',
               linewidths=2)
    texts = []
    for i, word in enumerate(top_word['word']):
        texts.append(ax.text(top_word['salience'].iloc[i], top_word['valence'].iloc[i], word, fontsize=15))
    
    adjust_text(texts, arrowprops=dict(arrowstyle='-', color='black'))
    # ax.set_xlim(2.65, 5.05)
    # ax.set_ylim(-1.1, 1.1)
    ax.set_xlabel('Salience')
    ax.set_ylabel('Valence')
    ax.axhline(y=0, color='gray', linestyle='--', alpha=0.5)
    ax.axvline(x=4, color='gray', linestyle='--', alpha=0.5)
    ax.set_title(title)


def create_figure(top_words_list, titles):
    """Arrange the scatter plots in a figure."""
    fig = plt.figure(figsize=(16, 12))
    gs = fig.add_gridspec(2, 2)
    # First row - all_top_word spanning two columns
    ax0 = fig.add_subplot(gs[0, :])
    plot_scatter(ax0, top_words_list[0], titles[0])
    # Second row
    ax1 = fig.add_subplot(gs[1, 0])
    plot_scatter(ax1, top_words_list[1], titles[1])
    ax2 = fig.add_subplot(gs[1, 1])
    plot_scatter(ax2, top_words_list[2], titles[2])
    
    plt.tight_layout()
    plt.show()

In [13]:
def create_POI_figure(top_words_list, titles):
    """Arrange the scatter plots in a figure."""
    fig = plt.figure(figsize=(18, 18))
    gs = fig.add_gridspec(3, 2)
    ax1 = fig.add_subplot(gs[0, 0])
    plot_scatter(ax1, top_words_list[0], titles[0])
    ax2 = fig.add_subplot(gs[0, 1])
    plot_scatter(ax2, top_words_list[1], titles[1])
    ax3 = fig.add_subplot(gs[1, 0])
    plot_scatter(ax3, top_words_list[2], titles[2])
    ax4 = fig.add_subplot(gs[1, 1])
    plot_scatter(ax4, top_words_list[3], titles[3])
    ax5 = fig.add_subplot(gs[2, 0])
    plot_scatter(ax5, top_words_list[4], titles[4])
    ax6 = fig.add_subplot(gs[2, 1])
    plot_scatter(ax6, top_words_list[5], titles[5])
    
    plt.tight_layout()
    plt.show()

POI_top_words_list = [restaurant_top_word, retail_top_word, recreation_top_word, hotel_top_word, service_top_word, healthcare_top_word]
categories = ['Restaurant', 'Retail Trade',  'Recreation', 'Hotel', 'Personal Service', 'Health Care']
create_POI_figure(POI_top_words_list, categories)

Bad pipe message: %s [b'live\r\nAccess-Control-Request-Method: GET\r\nAc', b'ss-Control-Request-Private-Network: true\r\nOrigin: https://api-d9c5afcf.duosecurity.com\r\nUser-Agent', b'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebK']
Bad pipe message: %s [b'/537.36 (KHTML, like Gecko) Chrome/127.0.0.0 Safari/537.36\r\nSec-Fetch-Mode: cors\r\nSec-Fetch-Site: cross-']
Bad pipe message: %s [b'ep-alive\r\nsec-ch-ua: "Not)A;Brand";v="99", "Google Chrome";v="127", "Chromium";v="127"\r\nAccept: text/plain', b'*/*; q=0.01\r\nsec-ch-ua-mobile: ?0\r\nUser-Age']
Bad pipe message: %s [b': Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/127.0.0.0 Saf']
Bad pipe message: %s [b'i/537.36\r\nsec-ch-ua-platform: "macOS"\r\nOrigin: https://api-d9c5afcf.duosecurity.com\r\nSec-Fetch-S']
Bad pipe message: %s [b'e: cross-site\r\nSec-Fetch-Mode: cors\r\nSec-Fetch-Dest: empty\r\nAccept-Encoding: gzip, deflate, br, zstd\r\nAc']
Bad pipe message: %s [b'live